# Хотя в некоторых заданиях просили нарисовать статическую карту, но в folium по умолчанию рисуется интерактивная. Для простоты я так и оставил, так как нарисовать статическую немного муторно

In [1]:
import numpy as np
import pandas as pd
import folium

import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

Чтобы сдать задание, выполните следующую последовательность действий.

1. Загрузите агрегированные данные о поездках в мае 2016. Просуммируйте общее количество поездок такси из каждой географической зоны и посчитайте количество ячеек, из которых в мае не было совершено ни одной поездки.
2. Нарисуйте статическую карту Нью-Йорка. Поставьте на карте точку там, где находится Эмпайр-Стейт-Билдинг.
3. Поверх статической карты Нью-Йорка визуализируйте данные о поездках из каждой ячейки так, чтобы цветовая шкала, в которую вы окрашиваете каждую ячейку, показывала суммарное количество поездок такси из неё.
4. Вставьте интерактивную карту Нью-Йорка — такую, которую можно прокручивать и увеличивать. Поставьте метку там, где находится статуя свободы.
5. Нарисуйте на интерактивной карте Нью-Йорка ячейки так, чтобы их цвет показывал среднее за месяц количество поездок такси в час из этой зоны.
6. Чтобы не выбирать из всех 2500 ячеек вручную, отфильтруйте ячейки, из которых в мае совершается в среднем меньше 5 поездок в час. Посчитайте количество оставшихся. Проверьте на карте, что среди этих ячеек нет таких, из которых поездки на самом деле невозможны.
7. Сохраните ноутбук в формате html, запакуйте ipynb и html в один архив и загрузите его в форму (html облегчит задачу проверки вашим рецензентам — в ipynb динамические карты часто не сохраняются, а для выполнения кода рецензентам придётся устанавливать все библиотеки).

1. Загрузите агрегированные данные о поездках в мае 2016. Просуммируйте общее количество поездок такси из каждой географической зоны и посчитайте количество ячеек, из которых в мае не было совершено ни одной поездки.

In [2]:
df = pd.read_csv('time_region_2016-05.csv', index_col='tpep_pickup_datetime')
df.head()

1  2  3  4  5  6  7  8  9  10  ...  2491  2492  2493  \
tpep_pickup_datetime                                 ...                     
2016-05-01 00:00:00   0  0  0  0  0  0  0  0  0   0  ...     0     0     0   
2016-05-01 01:00:00   0  0  0  0  0  0  0  0  0   0  ...     0     0     0   
2016-05-01 02:00:00   0  0  0  0  0  0  0  0  0   0  ...     0     0     0   
2016-05-01 03:00:00   0  0  0  0  0  0  0  0  0   0  ...     0     0     0   
2016-05-01 04:00:00   0  0  0  0  0  0  0  0  0   0  ...     0     0     0   

                      2494  2495  2496  2497  2498  2499  2500  
tpep_pickup_datetime                                            
2016-05-01 00:00:00      0     0     0     0     0     0     0  
2016-05-01 01:00:00      0     0     0     0     0     0     0  
2016-05-01 02:00:00      0     0     0     0     0     0     0  
2016-05-01 03:00:00      0     0     0     0     0     0     0  
2016-05-01 04:00:00      0     0     0     0     0     0     0  

[5 rows x 2500 columns]

In [3]:
trip_regions = df.sum(axis=0)
print('Ячеек, в которых не было сделано ни одной поездки:', (trip_regions == 0).sum())

Ячеек, в которых не было сделано ни одной поездки: 1283


2. Нарисуйте статическую карту Нью-Йорка. Поставьте на карте точку там, где находится Эмпайр-Стейт-Билдинг.

In [4]:
m = folium.Map(
    location=[40.74843, -73.98519],
    tiles='cartodbpositron',
    zoom_start=13,
)
folium.Marker([40.74843, -73.98519], popup='<i>Empire State Building</i>').add_to(m)
m

3. Поверх статической карты Нью-Йорка визуализируйте данные о поездках из каждой ячейки так, чтобы цветовая шкала, в которую вы окрашиваете каждую ячейку, показывала суммарное количество поездок такси из неё.

*На ячейку можно нажать и будет указан регион и количество поездок*

In [5]:
regions = pd.read_csv('regions.csv', sep=';')

In [6]:
for region, trips in trip_regions.items():
    bounds = regions.iloc[int(region) - 1, 1:5].values
    bounds = [
        [bounds[2], bounds[0]],
        [bounds[3], bounds[1]],
    ]
    folium.Rectangle(
        bounds=bounds,
        popup='region: {}, trips: {}'.format(region, trips),
        color='crimson',
        data=trips,
        fill=True,
        fill_opacity=trips / trip_regions.max()
    ).add_to(m)
m

4. Вставьте интерактивную карту Нью-Йорка — такую, которую можно прокручивать и увеличивать. Поставьте метку там, где находится статуя свободы.

In [7]:
liberty = folium.Map(
    location=[40.68924, -74.04454],
    tiles='cartodbpositron',
    zoom_start=13,
)
folium.Marker([40.68924, -74.04454], popup='<i>Statue of Liberty</i>').add_to(liberty)
liberty

5. Нарисуйте на интерактивной карте Нью-Йорка ячейки так, чтобы их цвет показывал среднее за месяц количество поездок такси в час из этой зоны.

In [8]:
mean_hour = folium.Map(
    location=[40.68924, -74.04454],
    tiles='cartodbpositron',
    zoom_start=13,
)

mean_hour_trip = df.mean()

for region, trips in mean_hour_trip.items():
    bounds = regions.iloc[int(region) - 1, 1:5].values
    bounds = [
        [bounds[2], bounds[0]],
        [bounds[3], bounds[1]],
    ]
    folium.Rectangle(
        bounds=bounds,
        popup='region: {}, trips: {}'.format(region, trips),
        color='crimson',
        data=trips,
        fill=True,
        fill_opacity=trips / mean_hour_trip.max()
    ).add_to(mean_hour)
mean_hour

6. Чтобы не выбирать из всех 2500 ячеек вручную, отфильтруйте ячейки, из которых в мае совершается в среднем меньше 5 поездок в час. Посчитайте количество оставшихся. Проверьте на карте, что среди этих ячеек нет таких, из которых поездки на самом деле невозможны.

In [9]:
mean_hour = folium.Map(
    location=[40.68924, -74.04454],
    tiles='cartodbpositron',
    zoom_start=13,
)

mean_hour_trip = df.mean()

for region, trips in mean_hour_trip.items():
    if trips < 5: continue
    
    bounds = regions.iloc[int(region) - 1, 1:5].values
    bounds = [
        [bounds[2], bounds[0]],
        [bounds[3], bounds[1]],
    ]
    folium.Rectangle(
        bounds=bounds,
        popup='region: {}, trips: {}'.format(region, trips),
        color='crimson',
        data=trips,
        fill=True,
        fill_opacity=trips / mean_hour_trip.max()
    ).add_to(mean_hour)
mean_hour

In [16]:
pd.DataFrame(mean_hour_trip[mean_hour_trip > 5].index).to_csv('big_regions.csv', index=False)

7. Сохраните ноутбук в формате html, запакуйте ipynb и html в один архив и загрузите его в форму (html облегчит задачу проверки вашим рецензентам — в ipynb динамические карты часто не сохраняются, а для выполнения кода рецензентам придётся устанавливать все библиотеки).

Сделано :)